#### Importamos dependencias

In [16]:
from requests.auth import HTTPBasicAuth
from impala.dbapi import connect #pip install impyla
from datetime import datetime
from pyhive import hive
import pandas as pd
import requests
import sqlparse
import json
import sys
import os
import re

In [17]:
'''Variables'''
## Atlas dev
headers = {
    "Content-Type": "application/json",
    "Accept": "application/json"
}
credentials = HTTPBasicAuth('atlasadmin', 'xNB8lZ!Dut')
atlas_urls = ["172.30.213.141","172.30.213.142"]
atlas_port = 31000

## Hive dev
hive_host = 'edh-master-01d.root.corp'
hive_port = 10000
hive_user = 'admin'


## Impala dev
impala_host = '172.30.213.211'
impala_port = 21050
impala_user = 'admin'

#### Para ejecutar SHOW CREATE TABLE en una sola tabla

In [18]:
#IMPALA
def show_create_table_impala( impala_database, table_name ):
    #Creo la conexión y obtengo el cursos
    impala_conn = connect(host=impala_host, port=impala_port, database=impala_database)
    impala_cursor = impala_conn.cursor()

    # Obtengo el create
    impala_cursor.execute(f'SHOW CREATE TABLE {impala_database}.{table_name}')
    databases = list(map(lambda x: x[0], impala_cursor.fetchall()))
    
    #Lo formateo a código ejecutable
    create_table_query = " ".join(databases)
    return create_table_query

In [10]:
#HIVE
def show_create_table( hive_database, table_name ):
    #Creo la conexión y obtengo el cursos
    hive_conn = hive.connect(host=hive_host, port=hive_port, username=hive_user, database=hive_database)
    hive_cursor = hive_conn.cursor()

    # Obtengo el create
    hive_cursor.execute(f'SHOW CREATE TABLE {hive_database}.{table_name}')
    databases = list(map(lambda x: x[0], hive_cursor.fetchall()))
    
    #Lo formateo a código ejecutable
    create_table_query = " ".join(databases)
    return create_table_query

In [67]:
# Data sin CREATE TABLE
df = pd.read_json("data/data.json")
df

de_ber_4con.productos_parametria_dim_productos  \
database                                               de_ber_4con   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT id_concepto AS id_concepto, cod_product...   
affected_tables  [de_ber_datamart_control_gestion.productos_pre...   

                    de_bsc_4con.productos_parametria_dim_productos  \
database                                               de_bsc_4con   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT id_concepto AS id_concepto, cod_product...   
affected_tables  [de_bsc_datamart_control_gestion.productos_pre...   

                    de_bsj_4con.productos_parametria_dim_productos  \
database                                               de_bsj_4con   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT id_concepto AS id_concepto, cod_product...   
affected_tables  [de_bsj_datamart_control_gestion.productos_pre...   

                    de_ber_3ref.productos_parametria_dim_productos  \
database                                               de_ber_3ref   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT COD_CONCE AS id_concepto,        COD_PR...   
affected_tables   [de_ber_4con.productos_parametria_dim_productos]   

                    de_bsc_3ref.productos_parametria_dim_productos  \
database                                               de_bsc_3ref   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT COD_CONCE AS id_concepto,        COD_PR...   
affected_tables   [de_bsc_4con.productos_parametria_dim_productos]   

                    de_bsj_3ref.productos_parametria_dim_productos  \
database                                               de_bsj_3ref   
table_name                      productos_parametria_dim_productos   
create_table                                                         
associated_term          productos_parametria_dim_productos_unisys   
loading_query    SELECT COD_CONCE AS id_concepto,        COD_PR...   
affected_tables   [de_bsj_4con.productos_parametria_dim_productos]   

                                       de_ber_2cur.productos_aampr  \
database                                               de_ber_2cur   
table_name                                         productos_aampr   
create_table                                                         
associated_term                                              aampr   
loading_query    SELECT cast(glb_dtime AS bigint) AS glb_dtime,...   
affected_tables  [de_ber_3ref.productos_parametria_dim_producto...   

                                       de_bsc_2cur.productos_aampr  \
database                                               de_bsc_2cur   
table_name                                         productos_aampr   
create_table                                                         
associated_term                                              aampr   
loading_query    SELECT cast(glb_dtime AS bigint) AS glb_dtime,...   
affected_tables  [de_bsc_3ref.productos_parametria_dim_producto...   

                                       de_bsj_2cur.productos_aampr  \
database              

In [21]:
with open('data/processed_data.json') as f:
    file = f.read()
    json_file = json.loads(file)

In [24]:
print(json.dumps(json_file, indent=2))

{
  "de_ber_4con.productos_parametria_dim_productos": {
    "database": "de_ber_4con",
    "table_name": "productos_parametria_dim_productos",
    "create_table": "CREATE EXTERNAL TABLE de_ber_4con.productos_parametria_dim_productos (\n  id_concepto TINYINT NOT NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'C\u00f3digo de concepto',\n  cod_producto SMALLINT NOT NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'C\u00f3digo de producto',\n  id_moneda TINYINT NOT NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'C\u00f3digo de moneda',\n  fecha_proceso VARCHAR(8) NOT NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'Fecha de proceso de la tabla de landing',\n  id_producto VARCHAR(10) NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'Identificaci\u00f3n del producto',\n  marca_sfb VARCHAR(1) NULL ENCODING AUTO_ENCODING COMPRESSION DEFAULT_COMPRESSION COMMENT 'Se\u00f1al que indica si es un pro

#### Poblar JSON con el 'CREATE TABLE' de cada tabla

In [13]:
# Poblar json de RAW a REF
'''
for table in json_file.keys():
    if '4con' not in table and 'datamart' not in table:
        db, table_name = table.split('.')
        table_create_with_properties = show_create_table( db, table_name )
        table_create = table_create_with_properties.split('TBLPROPERTIES')[0]
        
        json_file[table]['create_table'] = table_create
'''

In [23]:
# Poblar json en CON y DM
'''
for table in json_file.keys():
    if '1raw' not in table and '2cur' not in table and '3ref' not in table:
        db, table_name = table.split('.')
        table_create_with_properties = show_create_table_impala( db, table_name )
        
        json_file[table]['create_table'] = table_create_with_properties
'''

In [25]:
#GUARDAR ARCHIVO JSON
with open('data/processed_data.json', 'w') as file:
    json.dump(json_file, file, indent=4)